# Basic face recognizer using pre trained model

Below the is the implementation of a very basic face recognizer which can identify the face of the person showing on a web cam.
The implementation is inspired by two path breaking papers on facial recognition using deep convoluted neural network, namely FaceNet and DeepFace.

I have used pre trained model Keras-OpenFace which is an open source Keras implementation of the OpenFace (Originally Torch implemented) 

The pretrained model that I have used is by Victor Sy Wang's implementation and was loaded using his code: https://github.com/iwantooxxoox/Keras-OpenFace.

# Import the prerequisite libraries

We will be importing utils.py from https://github.com/iwantooxxoox/Keras-OpenFace/blob/master/utils.py (available with code) which contains utility functions to create the neural network and load the weights assoiated with it.

In [1]:
from keras.models import Sequential
from keras.layers import Conv2D, ZeroPadding2D, Activation, Input, concatenate
from keras.models import Model
from keras.layers.normalization import BatchNormalization
from keras.layers.pooling import MaxPooling2D, AveragePooling2D
from keras.layers.merge import Concatenate
from keras.layers.core import Lambda, Flatten, Dense
from keras.engine.topology import Layer
from keras import backend as K
import cv2
import os
import numpy as np
from numpy import genfromtxt
import pandas as pd
import tensorflow as tf
from utils import LRN2D
import utils

%load_ext autoreload
%autoreload 2

np.set_printoptions()

Using TensorFlow backend.


# Contructing the neural network model
The model here constructed is based on FaceNet's Inception model.

The implementation of model is available at: https://github.com/iwantooxxoox/Keras-OpenFace

In [2]:
myInput = Input(shape=(96, 96, 3))

x = ZeroPadding2D(padding=(3, 3), input_shape=(96, 96, 3))(myInput)
x = Conv2D(64, (7, 7), strides=(2, 2), name='conv1')(x)
x = BatchNormalization(axis=3, epsilon=0.00001, name='bn1')(x)
x = Activation('relu')(x)
x = ZeroPadding2D(padding=(1, 1))(x)
x = MaxPooling2D(pool_size=3, strides=2)(x)
x = Lambda(LRN2D, name='lrn_1')(x)
x = Conv2D(64, (1, 1), name='conv2')(x)
x = BatchNormalization(axis=3, epsilon=0.00001, name='bn2')(x)
x = Activation('relu')(x)
x = ZeroPadding2D(padding=(1, 1))(x)
x = Conv2D(192, (3, 3), name='conv3')(x)
x = BatchNormalization(axis=3, epsilon=0.00001, name='bn3')(x)
x = Activation('relu')(x)
x = Lambda(LRN2D, name='lrn_2')(x)
x = ZeroPadding2D(padding=(1, 1))(x)
x = MaxPooling2D(pool_size=3, strides=2)(x)

# Inception3a
inception_3a_3x3 = Conv2D(96, (1, 1), name='inception_3a_3x3_conv1')(x)
inception_3a_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_3x3_bn1')(inception_3a_3x3)
inception_3a_3x3 = Activation('relu')(inception_3a_3x3)
inception_3a_3x3 = ZeroPadding2D(padding=(1, 1))(inception_3a_3x3)
inception_3a_3x3 = Conv2D(128, (3, 3), name='inception_3a_3x3_conv2')(inception_3a_3x3)
inception_3a_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_3x3_bn2')(inception_3a_3x3)
inception_3a_3x3 = Activation('relu')(inception_3a_3x3)

inception_3a_5x5 = Conv2D(16, (1, 1), name='inception_3a_5x5_conv1')(x)
inception_3a_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_5x5_bn1')(inception_3a_5x5)
inception_3a_5x5 = Activation('relu')(inception_3a_5x5)
inception_3a_5x5 = ZeroPadding2D(padding=(2, 2))(inception_3a_5x5)
inception_3a_5x5 = Conv2D(32, (5, 5), name='inception_3a_5x5_conv2')(inception_3a_5x5)
inception_3a_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_5x5_bn2')(inception_3a_5x5)
inception_3a_5x5 = Activation('relu')(inception_3a_5x5)

inception_3a_pool = MaxPooling2D(pool_size=3, strides=2)(x)
inception_3a_pool = Conv2D(32, (1, 1), name='inception_3a_pool_conv')(inception_3a_pool)
inception_3a_pool = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_pool_bn')(inception_3a_pool)
inception_3a_pool = Activation('relu')(inception_3a_pool)
inception_3a_pool = ZeroPadding2D(padding=((3, 4), (3, 4)))(inception_3a_pool)

inception_3a_1x1 = Conv2D(64, (1, 1), name='inception_3a_1x1_conv')(x)
inception_3a_1x1 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_1x1_bn')(inception_3a_1x1)
inception_3a_1x1 = Activation('relu')(inception_3a_1x1)

inception_3a = concatenate([inception_3a_3x3, inception_3a_5x5, inception_3a_pool, inception_3a_1x1], axis=3)

# Inception3b
inception_3b_3x3 = Conv2D(96, (1, 1), name='inception_3b_3x3_conv1')(inception_3a)
inception_3b_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_3x3_bn1')(inception_3b_3x3)
inception_3b_3x3 = Activation('relu')(inception_3b_3x3)
inception_3b_3x3 = ZeroPadding2D(padding=(1, 1))(inception_3b_3x3)
inception_3b_3x3 = Conv2D(128, (3, 3), name='inception_3b_3x3_conv2')(inception_3b_3x3)
inception_3b_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_3x3_bn2')(inception_3b_3x3)
inception_3b_3x3 = Activation('relu')(inception_3b_3x3)

inception_3b_5x5 = Conv2D(32, (1, 1), name='inception_3b_5x5_conv1')(inception_3a)
inception_3b_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_5x5_bn1')(inception_3b_5x5)
inception_3b_5x5 = Activation('relu')(inception_3b_5x5)
inception_3b_5x5 = ZeroPadding2D(padding=(2, 2))(inception_3b_5x5)
inception_3b_5x5 = Conv2D(64, (5, 5), name='inception_3b_5x5_conv2')(inception_3b_5x5)
inception_3b_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_5x5_bn2')(inception_3b_5x5)
inception_3b_5x5 = Activation('relu')(inception_3b_5x5)

inception_3b_pool = Lambda(lambda x: x**2, name='power2_3b')(inception_3a)
inception_3b_pool = AveragePooling2D(pool_size=(3, 3), strides=(3, 3))(inception_3b_pool)
inception_3b_pool = Lambda(lambda x: x*9, name='mult9_3b')(inception_3b_pool)
inception_3b_pool = Lambda(lambda x: K.sqrt(x), name='sqrt_3b')(inception_3b_pool)
inception_3b_pool = Conv2D(64, (1, 1), name='inception_3b_pool_conv')(inception_3b_pool)
inception_3b_pool = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_pool_bn')(inception_3b_pool)
inception_3b_pool = Activation('relu')(inception_3b_pool)
inception_3b_pool = ZeroPadding2D(padding=(4, 4))(inception_3b_pool)

inception_3b_1x1 = Conv2D(64, (1, 1), name='inception_3b_1x1_conv')(inception_3a)
inception_3b_1x1 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_1x1_bn')(inception_3b_1x1)
inception_3b_1x1 = Activation('relu')(inception_3b_1x1)

inception_3b = concatenate([inception_3b_3x3, inception_3b_5x5, inception_3b_pool, inception_3b_1x1], axis=3)

# Inception3c
inception_3c_3x3 = utils.conv2d_bn(inception_3b,
                                   layer='inception_3c_3x3',
                                   cv1_out=128,
                                   cv1_filter=(1, 1),
                                   cv2_out=256,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(2, 2),
                                   padding=(1, 1))

inception_3c_5x5 = utils.conv2d_bn(inception_3b,
                                   layer='inception_3c_5x5',
                                   cv1_out=32,
                                   cv1_filter=(1, 1),
                                   cv2_out=64,
                                   cv2_filter=(5, 5),
                                   cv2_strides=(2, 2),
                                   padding=(2, 2))

inception_3c_pool = MaxPooling2D(pool_size=3, strides=2)(inception_3b)
inception_3c_pool = ZeroPadding2D(padding=((0, 1), (0, 1)))(inception_3c_pool)

inception_3c = concatenate([inception_3c_3x3, inception_3c_5x5, inception_3c_pool], axis=3)

#inception 4a
inception_4a_3x3 = utils.conv2d_bn(inception_3c,
                                   layer='inception_4a_3x3',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   cv2_out=192,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(1, 1),
                                   padding=(1, 1))
inception_4a_5x5 = utils.conv2d_bn(inception_3c,
                                   layer='inception_4a_5x5',
                                   cv1_out=32,
                                   cv1_filter=(1, 1),
                                   cv2_out=64,
                                   cv2_filter=(5, 5),
                                   cv2_strides=(1, 1),
                                   padding=(2, 2))

inception_4a_pool = Lambda(lambda x: x**2, name='power2_4a')(inception_3c)
inception_4a_pool = AveragePooling2D(pool_size=(3, 3), strides=(3, 3))(inception_4a_pool)
inception_4a_pool = Lambda(lambda x: x*9, name='mult9_4a')(inception_4a_pool)
inception_4a_pool = Lambda(lambda x: K.sqrt(x), name='sqrt_4a')(inception_4a_pool)
inception_4a_pool = utils.conv2d_bn(inception_4a_pool,
                                   layer='inception_4a_pool',
                                   cv1_out=128,
                                   cv1_filter=(1, 1),
                                   padding=(2, 2))
inception_4a_1x1 = utils.conv2d_bn(inception_3c,
                                   layer='inception_4a_1x1',
                                   cv1_out=256,
                                   cv1_filter=(1, 1))
inception_4a = concatenate([inception_4a_3x3, inception_4a_5x5, inception_4a_pool, inception_4a_1x1], axis=3)

#inception4e
inception_4e_3x3 = utils.conv2d_bn(inception_4a,
                                   layer='inception_4e_3x3',
                                   cv1_out=160,
                                   cv1_filter=(1, 1),
                                   cv2_out=256,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(2, 2),
                                   padding=(1, 1))
inception_4e_5x5 = utils.conv2d_bn(inception_4a,
                                   layer='inception_4e_5x5',
                                   cv1_out=64,
                                   cv1_filter=(1, 1),
                                   cv2_out=128,
                                   cv2_filter=(5, 5),
                                   cv2_strides=(2, 2),
                                   padding=(2, 2))
inception_4e_pool = MaxPooling2D(pool_size=3, strides=2)(inception_4a)
inception_4e_pool = ZeroPadding2D(padding=((0, 1), (0, 1)))(inception_4e_pool)

inception_4e = concatenate([inception_4e_3x3, inception_4e_5x5, inception_4e_pool], axis=3)

#inception5a
inception_5a_3x3 = utils.conv2d_bn(inception_4e,
                                   layer='inception_5a_3x3',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   cv2_out=384,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(1, 1),
                                   padding=(1, 1))

inception_5a_pool = Lambda(lambda x: x**2, name='power2_5a')(inception_4e)
inception_5a_pool = AveragePooling2D(pool_size=(3, 3), strides=(3, 3))(inception_5a_pool)
inception_5a_pool = Lambda(lambda x: x*9, name='mult9_5a')(inception_5a_pool)
inception_5a_pool = Lambda(lambda x: K.sqrt(x), name='sqrt_5a')(inception_5a_pool)
inception_5a_pool = utils.conv2d_bn(inception_5a_pool,
                                   layer='inception_5a_pool',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   padding=(1, 1))
inception_5a_1x1 = utils.conv2d_bn(inception_4e,
                                   layer='inception_5a_1x1',
                                   cv1_out=256,
                                   cv1_filter=(1, 1))

inception_5a = concatenate([inception_5a_3x3, inception_5a_pool, inception_5a_1x1], axis=3)

#inception_5b
inception_5b_3x3 = utils.conv2d_bn(inception_5a,
                                   layer='inception_5b_3x3',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   cv2_out=384,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(1, 1),
                                   padding=(1, 1))
inception_5b_pool = MaxPooling2D(pool_size=3, strides=2)(inception_5a)
inception_5b_pool = utils.conv2d_bn(inception_5b_pool,
                                   layer='inception_5b_pool',
                                   cv1_out=96,
                                   cv1_filter=(1, 1))
inception_5b_pool = ZeroPadding2D(padding=(1, 1))(inception_5b_pool)

inception_5b_1x1 = utils.conv2d_bn(inception_5a,
                                   layer='inception_5b_1x1',
                                   cv1_out=256,
                                   cv1_filter=(1, 1))
inception_5b = concatenate([inception_5b_3x3, inception_5b_pool, inception_5b_1x1], axis=3)

av_pool = AveragePooling2D(pool_size=(3, 3), strides=(1, 1))(inception_5b)
reshape_layer = Flatten()(av_pool)
dense_layer = Dense(128, name='dense_layer')(reshape_layer)
norm_layer = Lambda(lambda  x: K.l2_normalize(x, axis=1), name='norm_layer')(dense_layer)


# Final Model
model = Model(inputs=[myInput], outputs=norm_layer)

# Loading the model with pretrained weights

FaceNet is trained by minimizing the triplet loss. I will be  loading a previously trained model. weights are avaiable at https://github.com/iwantooxxoox/Keras-OpenFace in the "weights" folder which is also provided in this source.

This can take a couple of minutes to execute and depends on the speed of your machine.


In [3]:
# Load weights from csv files (which was exported from Openface torch model)
weights = utils.weights
weights_dict = utils.load_weights()

# Set layer weights of the model
for name in weights:
  if model.get_layer(name) != None:
    model.get_layer(name).set_weights(weights_dict[name])
  elif model.get_layer(name) != None:
    model.get_layer(name).set_weights(weights_dict[name])

## About <font color=blue>image_to_embedding</font> function        
When the model is loaded with pre trained weights, then we can create the **128 dimensional embedding vectors** for all the face images stored in the "images" folder. **"image_to_embedding"** function pass an image to the Inception network to generate the embedding vector.

In [4]:
def image_to_embedding(image, model):
    #image = cv2.resize(image, (96, 96), interpolation=cv2.INTER_AREA) 
    image = cv2.resize(image, (96, 96)) 
    img = image[...,::-1]
    img = np.around(np.transpose(img, (0,1,2))/255.0, decimals=12)
    x_train = np.array([img])
    embedding = model.predict_on_batch(x_train)
    return embedding


## About <font color=blue>recognize_face</font> function
This function calculate similarity between the captured image and the images that are already been stored. It passes the image to the trained neural network to generate its embedding vector. Which is then compared with all the embedding vectors of the images stored by calculating L2 Euclidean distance. 

If the minimum L2 distance between two embeddings is less than a threshpld (here I have taken the threashhold as .68 (which can be adjusted) then we have a match.

In [5]:
def recognize_face(face_image, input_embeddings, model):

    embedding = image_to_embedding(face_image, model)
    
    minimum_distance = 200
    name = None
    
    # Loop over  names and encodings.
    for (input_name, input_embedding) in input_embeddings.items():
        
       
        euclidean_distance = np.linalg.norm(embedding-input_embedding)
        

        print('Euclidean distance from %s is %s' %(input_name, euclidean_distance))

        
        if euclidean_distance < minimum_distance:
            minimum_distance = euclidean_distance
            name = input_name
    
    if minimum_distance < 0.68:
        return str(name)
    else:
        return None

## About <font color=blue>create_input_image_embeddings</font> function
This function generates 128 dimensional image ebeddings of all the images stored in the "images" directory by feed forwarding the images to a trained neural network. It creates a dictionary with key as the name of the face and value as embedding


## About <font color=blue>recognize_faces_in_cam</font> function
This function capture image from the webcam, detect a face in it and crop the image to have a face only, which is then passed to recognize_face function. 

In [6]:
import glob

def create_input_image_embeddings():
    input_embeddings = {}

    for file in glob.glob("images/*"):
        person_name = os.path.splitext(os.path.basename(file))[0]
        image_file = cv2.imread(file, 1)
        input_embeddings[person_name] = image_to_embedding(image_file, model)

    return input_embeddings

def recognize_faces_in_cam(input_embeddings):
    

    cv2.namedWindow("Face Recognizer")
    vc = cv2.VideoCapture(0)
   

    font = cv2.FONT_HERSHEY_SIMPLEX
    face_cascade = cv2.CascadeClassifier('haarcascade_frontalface_default.xml')
    
    
    while vc.isOpened():
        _, frame = vc.read()
        img = frame
        height, width, channels = frame.shape

        
        
        gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        faces = face_cascade.detectMultiScale(gray, 1.3, 5)

        # Loop through all the faces detected 
        identities = []
        for (x, y, w, h) in faces:
            x1 = x
            y1 = y
            x2 = x+w
            y2 = y+h

           
            
            face_image = frame[max(0, y1):min(height, y2), max(0, x1):min(width, x2)]    
            identity = recognize_face(face_image, input_embeddings, model)
            
            

            if identity is not None:
                img = cv2.rectangle(frame,(x1, y1),(x2, y2),(255,255,255),2)
                cv2.putText(img, str(identity), (x1+5,y1-5), font, 1, (255,255,255), 2)
        
        key = cv2.waitKey(100)
        cv2.imshow("Face Recognizer", img)

        if key == 27: # exit on ESC
            break
    vc.release()
    cv2.destroyAllWindows()

## Capturing the face image
Following code captures 10 face images of the person. They all are stored in **"images"** folder with the name User_1 to User_10. Select a good captured image from the set of 10 images. Rename it with the name of person and delete rest of them. This image will be used for recognizing the the identity of the person using one shot learning.

In [7]:
cam = cv2.VideoCapture(0)

face_detector = cv2.CascadeClassifier('haarcascade_frontalface_default.xml')

count = 0
while(True):
    ret, img = cam.read()
    #gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    faces = face_detector.detectMultiScale(img, 1.3, 5)
    for (x,y,w,h) in faces:
        x1 = x
        y1 = y
        x2 = x+w
        y2 = y+h
        cv2.rectangle(img, (x1,y1), (x2,y2), (255,255,255), 2)     
        count += 1
        # Save the captured image into the datasets folder
        cv2.imwrite("images/User_" + str(count) + ".jpg", img[y1:y2,x1:x2])
        cv2.imshow('image', img)
    k = cv2.waitKey(200) & 0xff # Press 'ESC' for exiting video
    if k == 27:
        break
    elif count >= 10: # Take 30 face sample and stop video
         break
cam.release()
cv2.destroyAllWindows()

# Lets run the face recognizer program :-)

In [8]:
input_embeddings = create_input_image_embeddings()
recognize_faces_in_cam(input_embeddings)


Euclidean distance from 0206CS171087_29 is 0.11995371
Euclidean distance from 0206CS171092_4 is 0.1386778
Euclidean distance from 0206CS171102_23 is 0.07621312
Euclidean distance from 0206CS171087_15 is 0.11321641
Euclidean distance from 0206CS171115_13 is 0.12778005
Euclidean distance from 0206CS171092_20 is 0.13943428
Euclidean distance from 0206CS171117_16 is 0.08433744
Euclidean distance from 0206CS171117_1 is 0.1301193
Euclidean distance from 0206CS171087_8 is 0.122540325
Euclidean distance from 0206CS171115_3 is 0.1253598
Euclidean distance from 0206CS171115_2 is 0.13142854
Euclidean distance from 0206CS171087_9 is 0.098399304
Euclidean distance from 0206CS171117_17 is 0.08766977
Euclidean distance from 0206CS171092_21 is 0.11459842
Euclidean distance from 0206CS171115_12 is 0.12690467
Euclidean distance from 0206CS171087_14 is 0.12227118
Euclidean distance from 0206CS171092_5 is 0.13845894
Euclidean distance from 0206CS171087_28 is 0.12049082
Euclidean distance from 0206CS171102

Euclidean distance from 0206CS171087_29 is 0.11608761
Euclidean distance from 0206CS171092_4 is 0.13627973
Euclidean distance from 0206CS171102_23 is 0.06286328
Euclidean distance from 0206CS171087_15 is 0.10863894
Euclidean distance from 0206CS171115_13 is 0.111772664
Euclidean distance from 0206CS171092_20 is 0.13458581
Euclidean distance from 0206CS171117_16 is 0.063206375
Euclidean distance from 0206CS171117_1 is 0.1324728
Euclidean distance from 0206CS171087_8 is 0.10444632
Euclidean distance from 0206CS171115_3 is 0.11124983
Euclidean distance from 0206CS171115_2 is 0.12322355
Euclidean distance from 0206CS171087_9 is 0.095148996
Euclidean distance from 0206CS171117_17 is 0.0654582
Euclidean distance from 0206CS171092_21 is 0.10312005
Euclidean distance from 0206CS171115_12 is 0.111398585
Euclidean distance from 0206CS171087_14 is 0.10382192
Euclidean distance from 0206CS171092_5 is 0.13643841
Euclidean distance from 0206CS171087_28 is 0.10281467
Euclidean distance from 0206CS171

Euclidean distance from 0206CS171087_29 is 0.107035086
Euclidean distance from 0206CS171092_4 is 0.13935456
Euclidean distance from 0206CS171102_23 is 0.059075203
Euclidean distance from 0206CS171087_15 is 0.09981649
Euclidean distance from 0206CS171115_13 is 0.11014371
Euclidean distance from 0206CS171092_20 is 0.13785644
Euclidean distance from 0206CS171117_16 is 0.055721648
Euclidean distance from 0206CS171117_1 is 0.1377622
Euclidean distance from 0206CS171087_8 is 0.099098474
Euclidean distance from 0206CS171115_3 is 0.112590715
Euclidean distance from 0206CS171115_2 is 0.12632766
Euclidean distance from 0206CS171087_9 is 0.088170975
Euclidean distance from 0206CS171117_17 is 0.05586895
Euclidean distance from 0206CS171092_21 is 0.104772426
Euclidean distance from 0206CS171115_12 is 0.11007695
Euclidean distance from 0206CS171087_14 is 0.098460734
Euclidean distance from 0206CS171092_5 is 0.14044026
Euclidean distance from 0206CS171087_28 is 0.09836106
Euclidean distance from 0206

Euclidean distance from 0206CS171087_29 is 0.11164823
Euclidean distance from 0206CS171092_4 is 0.1422215
Euclidean distance from 0206CS171102_23 is 0.061144345
Euclidean distance from 0206CS171087_15 is 0.103788346
Euclidean distance from 0206CS171115_13 is 0.11304051
Euclidean distance from 0206CS171092_20 is 0.14077912
Euclidean distance from 0206CS171117_16 is 0.05717041
Euclidean distance from 0206CS171117_1 is 0.14057258
Euclidean distance from 0206CS171087_8 is 0.086944446
Euclidean distance from 0206CS171115_3 is 0.11710321
Euclidean distance from 0206CS171115_2 is 0.1295439
Euclidean distance from 0206CS171087_9 is 0.09271698
Euclidean distance from 0206CS171117_17 is 0.055199783
Euclidean distance from 0206CS171092_21 is 0.095991015
Euclidean distance from 0206CS171115_12 is 0.11249465
Euclidean distance from 0206CS171087_14 is 0.08591888
Euclidean distance from 0206CS171092_5 is 0.14331713
Euclidean distance from 0206CS171087_28 is 0.08635351
Euclidean distance from 0206CS17

Euclidean distance from 0206CS171087_29 is 0.119938254
Euclidean distance from 0206CS171092_4 is 0.14854163
Euclidean distance from 0206CS171102_23 is 0.07308507
Euclidean distance from 0206CS171087_15 is 0.11236113
Euclidean distance from 0206CS171115_13 is 0.114761874
Euclidean distance from 0206CS171092_20 is 0.14547358
Euclidean distance from 0206CS171117_16 is 0.05499837
Euclidean distance from 0206CS171117_1 is 0.15480247
Euclidean distance from 0206CS171087_8 is 0.07915025
Euclidean distance from 0206CS171115_3 is 0.11939751
Euclidean distance from 0206CS171115_2 is 0.13581401
Euclidean distance from 0206CS171087_9 is 0.10241494
Euclidean distance from 0206CS171117_17 is 0.052691832
Euclidean distance from 0206CS171092_21 is 0.08896035
Euclidean distance from 0206CS171115_12 is 0.114422575
Euclidean distance from 0206CS171087_14 is 0.078302264
Euclidean distance from 0206CS171092_5 is 0.14959548
Euclidean distance from 0206CS171087_28 is 0.078090996
Euclidean distance from 0206C

...

Euclidean distance from 0206CS171087_29 is 0.14348993
Euclidean distance from 0206CS171092_4 is 0.1714711
Euclidean distance from 0206CS171102_23 is 0.12473487
Euclidean distance from 0206CS171087_15 is 0.14012055
Euclidean distance from 0206CS171115_13 is 0.11910188
Euclidean distance from 0206CS171092_20 is 0.16573781
Euclidean distance from 0206CS171117_16 is 0.106177785
Euclidean distance from 0206CS171117_1 is 0.1854524
Euclidean distance from 0206CS171087_8 is 0.11524351
Euclidean distance from 0206CS171115_3 is 0.1342851
Euclidean distance from 0206CS171115_2 is 0.15780687
Euclidean distance from 0206CS171087_9 is 0.14343672
Euclidean distance from 0206CS171117_17 is 0.103295326
Euclidean distance from 0206CS171092_21 is 0.1348971
Euclidean distance from 0206CS171115_12 is 0.11968614
Euclidean distance from 0206CS171087_14 is 0.11417957
Euclidean distance from 0206CS171092_5 is 0.17518781
Euclidean distance from 0206CS171087_28 is 0.116659835
Euclidean distance from 0206CS171102

Euclidean distance from 0206CS171087_29 is 0.16087745
Euclidean distance from 0206CS171092_4 is 0.18340285
Euclidean distance from 0206CS171102_23 is 0.12535533
Euclidean distance from 0206CS171087_15 is 0.15630558
Euclidean distance from 0206CS171115_13 is 0.15405071
Euclidean distance from 0206CS171092_20 is 0.18209188
Euclidean distance from 0206CS171117_16 is 0.11906309
Euclidean distance from 0206CS171117_1 is 0.19561243
Euclidean distance from 0206CS171087_8 is 0.06349749
Euclidean distance from 0206CS171115_3 is 0.16312553
Euclidean distance from 0206CS171115_2 is 0.17722087
Euclidean distance from 0206CS171087_9 is 0.15108149
Euclidean distance from 0206CS171117_17 is 0.11326413
Euclidean distance from 0206CS171092_21 is 0.10528539
Euclidean distance from 0206CS171115_12 is 0.15350032
Euclidean distance from 0206CS171087_14 is 0.061022945
Euclidean distance from 0206CS171092_5 is 0.18575893
Euclidean distance from 0206CS171087_28 is 0.06531655
Euclidean distance from 0206CS1711

Euclidean distance from 0206CS171087_29 is 0.15788081
Euclidean distance from 0206CS171092_4 is 0.17150511
Euclidean distance from 0206CS171102_23 is 0.11339051
Euclidean distance from 0206CS171087_15 is 0.15315846
Euclidean distance from 0206CS171115_13 is 0.1484171
Euclidean distance from 0206CS171092_20 is 0.17016114
Euclidean distance from 0206CS171117_16 is 0.111793175
Euclidean distance from 0206CS171117_1 is 0.1846296
Euclidean distance from 0206CS171087_8 is 0.04521776
Euclidean distance from 0206CS171115_3 is 0.15615408
Euclidean distance from 0206CS171115_2 is 0.16710791
Euclidean distance from 0206CS171087_9 is 0.14481914
Euclidean distance from 0206CS171117_17 is 0.10625501
Euclidean distance from 0206CS171092_21 is 0.09720393
Euclidean distance from 0206CS171115_12 is 0.14835027
Euclidean distance from 0206CS171087_14 is 0.04306075
Euclidean distance from 0206CS171092_5 is 0.17376399
Euclidean distance from 0206CS171087_28 is 0.048481107
Euclidean distance from 0206CS17110

Euclidean distance from 0206CS171087_29 is 0.13346274
Euclidean distance from 0206CS171092_4 is 0.17578238
Euclidean distance from 0206CS171102_23 is 0.1483818
Euclidean distance from 0206CS171087_15 is 0.13292511
Euclidean distance from 0206CS171115_13 is 0.112157375
Euclidean distance from 0206CS171092_20 is 0.16774616
Euclidean distance from 0206CS171117_16 is 0.12775004
Euclidean distance from 0206CS171117_1 is 0.19109438
Euclidean distance from 0206CS171087_8 is 0.16594647
Euclidean distance from 0206CS171115_3 is 0.12648828
Euclidean distance from 0206CS171115_2 is 0.1544422
Euclidean distance from 0206CS171087_9 is 0.14637251
Euclidean distance from 0206CS171117_17 is 0.12738004
Euclidean distance from 0206CS171092_21 is 0.17212467
Euclidean distance from 0206CS171115_12 is 0.11327854
Euclidean distance from 0206CS171087_14 is 0.16501191
Euclidean distance from 0206CS171092_5 is 0.17951992
Euclidean distance from 0206CS171087_28 is 0.16688702
Euclidean distance from 0206CS171102

Euclidean distance from 0206CS171087_29 is 0.11612224
Euclidean distance from 0206CS171092_4 is 0.16713852
Euclidean distance from 0206CS171102_23 is 0.1343762
Euclidean distance from 0206CS171087_15 is 0.11556055
Euclidean distance from 0206CS171115_13 is 0.10992307
Euclidean distance from 0206CS171092_20 is 0.16110192
Euclidean distance from 0206CS171117_16 is 0.11014121
Euclidean distance from 0206CS171117_1 is 0.18361093
Euclidean distance from 0206CS171087_8 is 0.14228506
Euclidean distance from 0206CS171115_3 is 0.12327492
Euclidean distance from 0206CS171115_2 is 0.15030657
Euclidean distance from 0206CS171087_9 is 0.1260721
Euclidean distance from 0206CS171117_17 is 0.10810984
Euclidean distance from 0206CS171092_21 is 0.15001342
Euclidean distance from 0206CS171115_12 is 0.10952681
Euclidean distance from 0206CS171087_14 is 0.14123978
Euclidean distance from 0206CS171092_5 is 0.17117302
Euclidean distance from 0206CS171087_28 is 0.14332484
Euclidean distance from 0206CS171102_